In [1]:
import numpy as np
import json
import pandas as pd

with open('processed_data/baseData.json','r') as f:
    data = json.load(f)

data = pd.DataFrame(data)


HOST_FLAG ={
    'GRE': 1896,
    'FRA': 1900,
    'USA': 1904,
    'GBR': 1908,
    'SWE': 1912,
    'BEL': 1920,
    'FRA': 1924,
    'NED': 1928,
    'USA': 1932,
    'GER': 1936,
    'BEL': 1948,
    'FIN': 1952,
    'AUS': 1956,
    'ITA': 1960,
    'JPN': 1964,
    'MEX': 1968,
    'GER': 1972,
    'CAN': 1976,
    'URS': 1980,
    'USA': 1984,
    'KOR': 1988,
    'ESP': 1992,
    'USA': 1996,
    'AUS': 2000,
    'GRE': 2004,
    'CHN': 2008,
    'GBR': 2012,
    'BRA': 2016,
    'JPN': 2020,
    'FRA': 2024,
    'USA': 2028,
    'AUS': 2032
}

B = data['NOC'].unique()
A = HOST_FLAG.keys()

A = set(A)
B = set(B)

for i in A:
    if i not in B:
        print(i)

# print(data.head())




In [2]:
import pandas as pd

# 假设 data 是你提供的数据框
# 1. 统计每个 Name 对应的 Sex 的不同数量
duplicates = data.groupby('Name')['Sex'].nunique()

# 2. 筛选出 Sex 数量大于 1 的 Name，即存在 Sex 不同的 Name
conflicting_names = duplicates[duplicates > 1].index

# 3. 通过过滤冲突的 Name 输出对应的行
conflicting_rows = data[data['Name'].isin(conflicting_names)]

# 打印冲突的行
print(conflicting_rows)


               Name Sex       Team  NOC  Year            City  \
4127      Ahmed Ali   M      Egypt  EGY  1996         Atlanta   
4129      Ahmed Ali   M      Sudan  SUD  2016  Rio de Janeiro   
4131      Ahmed Ali   M      Egypt  EGY  1948          London   
4132      Ahmed Ali   M      Egypt  EGY  1948          London   
4133      Ahmed Ali   M      Egypt  EGY  1948          London   
...             ...  ..        ...  ...   ...             ...   
246075     Liu Yang   F      China  CHN  2024           Paris   
247410  Alex Wilson   F  Australia  AUS  2024           Paris   
248124   Jiajun Sun   M      China  CHN  2024           Paris   
248125   Jiajun Sun   M      China  CHN  2024           Paris   
248126   Jiajun Sun   M      China  CHN  2024           Paris   

                   Sport                                   Event     Medal  
4127          [Handball]                 Handball Men's Handball  No medal  
4129         [Athletics]              Athletics Men's 200 metres 

In [3]:
data['HOST_FLAG'] = data.apply(lambda row: 1 if HOST_FLAG.get(row['NOC']) == row['Year'] else 0, axis=1)
print(data['HOST_FLAG'].value_counts())


HOST_FLAG
0    243662
1      8903
Name: count, dtype: int64


In [4]:
def map_sport(sports):
    mapping = {
        'Trampoline Gymnastics': 'Trampolining',
        'Artistic Gymnastics': 'Gymnastics',
        'Cycling Track': 'Cycling',
        'Cycling Road': 'Cycling',
        'Cycling Mountain Bike': 'Cycling',
        'Cycling BMX Racing': 'Cycling',
        'Cycling BMX Freestyle': 'Cycling',
        'Artistic Swimming': 'Synchronized Swimming',
        'Canoe Sprint': 'Canoeing',
        'Canoe Slalom': 'Canoeing',
        'Equestrian': 'Equestrianism'
    }
    return [mapping.get(sport, sport) for sport in sports]

data['Sport'] = data['Sport'].apply(map_sport)

data.to_json("processed_data/baseData.json")

In [5]:
# for row in data.itertuples():
#     if 'Cycling Mountain Bike' in row.Sport:
#         print(row)


In [6]:
unique_sports = []

for row in data.itertuples():
    unique_sports.extend(row.Sport)

unique_sports = set(unique_sports)
print(unique_sports)
print(len(unique_sports))


{'Tennis', 'Motorboating', 'Basketball', 'Marathon Swimming', 'Water Polo', 'Trampolining', 'Badminton', 'Tug-Of-War', 'Polo', 'Basque Pelota', 'Rugby', 'Taekwondo', 'Sailing', 'Softball', 'Lacrosse', 'Rowing', 'Croquet', 'Athletics', 'Synchronized Swimming', 'Cricket', 'Alpinism', 'Archery', 'Wrestling', 'Baseball', 'Ice Hockey', 'Sport Climbing', 'Breaking', 'Cycling', 'Figure Skating', 'Fencing', 'Equestrianism', 'Beach Volleyball', 'Surfing', 'Swimming', 'Volleyball', 'Weightlifting', 'Hockey', 'Aeronautics', 'Judo', 'Rhythmic Gymnastics', 'Baseball/Softball', '3x3 Basketball', 'Rugby Sevens', 'Roque', 'Skateboarding', 'Shooting', 'Jeu De Paume', 'Triathlon', 'Handball', 'Art Competitions', 'Modern Pentathlon', 'Boxing', 'Gymnastics', 'Diving', 'Racquets', 'Karate', 'Football', 'Canoeing', 'Golf', 'Table Tennis'}
60


In [7]:
sport_counts = {}

for sport in unique_sports:
    count = data['Sport'].apply(lambda x: sport in x).sum()
    sport_counts[sport] = count

sport_counts = sorted(sport_counts.items(), key=lambda x: x[1], reverse=True)
print(sport_counts)

sport_start_time = {}
sport_end_time = {}

for sport in unique_sports:
    start_time = 9999
    end_time = 1986
    for row in data.itertuples():
        if sport in row.Sport:
            end_time = max(end_time,row.Year)
            start_time = min(start_time,row.Year)
    sport_end_time[sport] = end_time
    sport_start_time[sport] = start_time

print(sport_start_time)
print(sport_end_time)

summary_df = pd.DataFrame({
    'Sport': [sport for sport, count in sport_counts],
    'Count': [count for sport, count in sport_counts],
    'Start Year': [sport_start_time[sport] for sport, _ in sport_counts],
    'End Year': [sport_end_time[sport] for sport, _ in sport_counts]
})
print(summary_df)
summary_df.to_csv('processed_data/sport_summary.csv',index=False)






[('Athletics', np.int64(43294)), ('Gymnastics', np.int64(29004)), ('Swimming', np.int64(26468)), ('Shooting', np.int64(12580)), ('Cycling', np.int64(12567)), ('Rowing', np.int64(11625)), ('Fencing', np.int64(11558)), ('Football', np.int64(7906)), ('Wrestling', np.int64(7734)), ('Sailing', np.int64(7266)), ('Canoeing', np.int64(7183)), ('Equestrianism', np.int64(7179)), ('Boxing', np.int64(6584)), ('Hockey', np.int64(6264)), ('Basketball', np.int64(5112)), ('Judo', np.int64(4876)), ('Handball', np.int64(4419)), ('Water Polo', np.int64(4418)), ('Weightlifting', np.int64(4256)), ('Volleyball', np.int64(4003)), ('Art Competitions', np.int64(3578)), ('Tennis', np.int64(3446)), ('Diving', np.int64(3193)), ('Archery', np.int64(2846)), ('Table Tennis', np.int64(2480)), ('Modern Pentathlon', np.int64(1821)), ('Badminton', np.int64(1816)), ('Synchronized Swimming', np.int64(1166)), ('Rugby Sevens', np.int64(928)), ('Baseball', np.int64(894)), ('Taekwondo', np.int64(870)), ('Rhythmic Gymnastics',

In [8]:
athletes = data['Name'].unique()
print(athletes)
json.dump(athletes.tolist(),open('processed_data/athletes.json','w'))
sports = summary_df['Sport'].unique()
print(sports)
json.dump(sports.tolist(),open('processed_data/sports.json','w'))


['A Dijiang' 'A Lamusi' 'Gunnar Aaby' ... 'Emanuela Liuzzi' 'Isayah Boers'
 'Charlie Carvell']
['Athletics' 'Gymnastics' 'Swimming' 'Shooting' 'Cycling' 'Rowing'
 'Fencing' 'Football' 'Wrestling' 'Sailing' 'Canoeing' 'Equestrianism'
 'Boxing' 'Hockey' 'Basketball' 'Judo' 'Handball' 'Water Polo'
 'Weightlifting' 'Volleyball' 'Art Competitions' 'Tennis' 'Diving'
 'Archery' 'Table Tennis' 'Modern Pentathlon' 'Badminton'
 'Synchronized Swimming' 'Rugby Sevens' 'Baseball' 'Taekwondo'
 'Rhythmic Gymnastics' 'Triathlon' 'Beach Volleyball' 'Golf' 'Softball'
 'Baseball/Softball' 'Trampolining' 'Tug-Of-War' 'Skateboarding' 'Rugby'
 'Marathon Swimming' '3x3 Basketball' 'Sport Climbing' 'Polo' 'Surfing'
 'Karate' 'Lacrosse' 'Ice Hockey' 'Figure Skating' 'Breaking' 'Cricket'
 'Croquet' 'Motorboating' 'Racquets' 'Jeu De Paume' 'Alpinism' 'Roque'
 'Basque Pelota' 'Aeronautics']


In [9]:

finalTrainData = {}

# for row in data.itertuples():
#     if row.Name not in finalTrainData:
#         finalTrainData[row.Name] = {}
    
#     for sport in row.Sport:
#         if sport not in finalTrainData[row.Name]:
#             finalTrainData[row.Name][sport] = []
#         finalTrainData[row.Name][sport].append(row.Year)

for row in data.itertuples():
    for sport in row.Sport:
        if sport not in finalTrainData:
            finalTrainData[sport] = {}

        sex = 0 if row.Sex == 'F' else 1
        if sex not in finalTrainData[sport]:
            finalTrainData[sport][sex] = {}
        if row.Name not in finalTrainData[sport][sex]:
            finalTrainData[sport][sex][row.Name] = {}
        if row.Medal == 'No medal': 
            finalTrainData[sport][sex][row.Name][row.Year] = [0,row.HOST_FLAG]
        elif row.Medal == 'Bronze':
            finalTrainData[sport][sex][row.Name][row.Year]  = [1,row.HOST_FLAG]
        elif row.Medal == 'Silver':
            finalTrainData[sport][sex][row.Name][row.Year]  = [2,row.HOST_FLAG]
        elif row.Medal == 'Gold':
            finalTrainData[sport][sex][row.Name][row.Year]  = [3,row.HOST_FLAG]

print(finalTrainData)

json.dump(finalTrainData,open('processed_data/initialTrainData.json','w'))


{'Basketball': {1: {'A Dijiang': {1992: [0, 0]}, 'Youssef Abbas': {1952: [0, 0]}, 'Alessandro Abbio': {2000: [0, 0]}, 'Ahmed Mobarak': {1972: [0, 0]}, 'Amir Meguid': {1984: [0, 0], 1988: [0, 0]}, 'Awad Awad': {1972: [0, 0], 1976: [0, 0]}, 'Alaa Abdoun': {1988: [0, 0]}, 'Julius Abdur-rahim': {2000: [3, 0]}, 'Shigeaki Abe': {1972: [0, 0], 1976: [0, 0]}, 'Essameldin El-nein': {1984: [0, 0]}, 'Youssef Ouf': {1948: [0, 0], 1952: [0, 0]}, 'Pedro Pascal': {1980: [0, 0]}, 'Alejandro Redondo': {2016: [1, 0]}, 'Emilio Achacoso': {1960: [0, 0]}, 'Kieron Achara': {2012: [0, 1]}, 'Martn Daz': {1948: [0, 0], 1952: [1, 0]}, 'ngel Lizana': {1948: [0, 0]}, 'Roberto Acua': {2016: [0, 0]}, 'Adilson Nascimento': {1972: [0, 0], 1980: [0, 0], 1984: [0, 0]}, 'Hamdi Ibrahim': {1976: [0, 0]}, 'Dainius Adomaitis': {2000: [1, 0]}, 'William Adornado': {1972: [0, 0]}, 'Rubn Melndez': {1964: [0, 0], 1968: [0, 0]}, 'Hamed Eslamieh': {2008: [0, 0]}, 'Arturo Agard': {1968: [0, 0]}, 'Gregorio Muruzabal': {1936: [0, 0]}

In [ ]:
with open('processed_data/athletes.json','r') as f:
    athletes = json.load(f)

with open("processed_data/sports.json","r") as f:
    sports = json.load(f)

with open("processed_data/initialTrainData.json","r") as f:
    initialData = json.load(f)

Data = {}

N0 = {}


for sport in sports:
    Data[sport] = []
    N0[sport] = 0
    total = 0
    for idx,sex in initialData[sport].items():
        
        for key,athlete in sex.items():
            total += 1
            if len(athlete) <= 0:
                print("len<=0")
                continue
            elif len(athlete) == 1:
                N0[sport] += 1
            else:
                sortedData = sorted(athlete.items(),key=lambda x:x[0])
                simpleData = [-1,-1]

                hostF = 0 if sortedData[0][1][1] == 1 else -1
                simpleData.append(sortedData[0][1][0])
                for i in range(1,len(sortedData)):
                    # print(type(sortedData[i-1][0]))
                    if int(sortedData[i-1][0]) +4 != int(sortedData[i][0]):
                        break
                    simpleData.append(sortedData[i][1][0])
                    hostF = i if hostF==-1 and sortedData[i][1][1] == 1 else hostF

                print(simpleData)
                if len(simpleData) > 3:
                    temp_list = [sex,hostF]
                    for i in range(len(simpleData)-3):
                        a = temp_list+simpleData[i:i+4]
                        print(a)
                        # print(simpleData[i:i+4])
                        Data[sport].append(a)

    N0[sport] = N0[sport]/total                   
            

print(Data)
json.dump(Data,open("processed_data/finalData2.json","w"))
json.dump(N0,open("processed_data/N02.json","w"))
